In [1]:

from Carcassonne_Game.Carcassonne import CarcassonneState
from TicTacToe_Game.TicTacToe import TicTacToeState 
from Function_Optimisation_Game.Function_Optimisation import FunctionOptimisationState
from player.Player import RandomPlayer
from player.MCTS_Player import MCTSPlayer
from player.MCTS_RAVE_Player import MCTS_RAVEPlayer
from player.MCTS_ES_BACK_Player import MCTS_ES_BACK_Player
from player.MCTS_ES_BACK_SEM_Player import MCTS_ES_BACK_SEM_Player

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import os
import pandas as pd
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import numpy as np
import ast
import random
import math
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
from scipy.stats import bernoulli


In [3]:
#https://plotly.com/python/mapbox-density-heatmaps/
#https://plotly.com/python/v3/density-plots/
#https://plotly.com/python/imshow/
#https://plotly.com/python/mapbox-density-hea
#https://plotly.com/python/histograms/
#https://plotly.com/python/subplots/

def func(x): 
   return 0.5 + 0.5*math.sin(20*x[0])
def func2(x): 
   return (0.5+0.5*math.sin(20*x[0]))*(0.5+0.5*math.sin(20*x[1]))
def func3(x): return x*x
def func4(x): return abs(math.sin(1/math.pow(x[0]-0.5,2)))
def func5(x): #from the paper
   if x[0] < 0.5:
      return 0.5+0.5*abs(math.sin(1/pow(x[0],5)))
   else:
      return 7/20+0.5*abs(math.sin(1/pow(x[0],5)))

ranges = [[0,1]]
iterations = 20000
lamb = 4
ngen = 20
es_sims = 30
mcts_player = MCTSPlayer(iterations=iterations
                        ,c_param = 1#math.sqrt(2), 
                        ,name='MCTS_sq2_100')
mcts_player = MCTS_ES_BACK_SEM_Player(iterations=iterations-(lamb*ngen*es_sims)
                        ,c_param=1
                        ,Lambda=lamb
                        ,NGen=ngen
                        ,ES_Sims=es_sims
                        ,ESType="comma")
random_player = RandomPlayer()
state = FunctionOptimisationState(players=[mcts_player], function=func5, ranges=ranges, splits=5)
#state = FunctionOptimisationState(players=[random_player], function=func2, ranges=[[0,1],[0,1]], splits=3, minimum_step=0.0000001)
m = mcts_player.chooseAction(state)

def show_search(mcts_player, function, dimension=0, n_buckets = 100, type="divisions", divisions = 3):
   #data = pd.DataFrame(columns=["id","x","id_block"])
   id_list = []
   x_list = []
   id_block_list = []
   n_nodes = len(mcts_player.nodes_dict)
   #print(n_nodes)
   for key,node in mcts_player.nodes_dict.items():
      id_list.append(node.id)
      x_list.append(node.state.eval_point()[dimension])
      id_block_list.append(int((node.id/n_nodes)/(1/divisions)))
      #data.add(add_dict)
   data_dict = {"id":id_list, "x":x_list, "id_block":id_block_list}
   data = pd.DataFrame(data_dict)

   fig = make_subplots(rows=2, cols=1,shared_xaxes=True,vertical_spacing=0.02,row_heights=[0.6,0.4])
   #fig.add_trace(px.histogram(data, x="x", color="id_block", nbins=n_buckets),row=1,col=1)
   for div in range(divisions+1):
      temp_data = data.loc[data["id_block"]==div]
      fig.add_trace(go.Histogram(x=temp_data.x, nbinsx=n_buckets),row=1,col=1)

   fig.update_layout(barmode='stack')
   x = np.linspace(0.001,1,5000)
   y = [function([i]) for i in x]
   fig.add_trace(go.Scatter(x=x, y=y),row=2,col=1)
   fig.show()


show_search(mcts_player, func5)




(ES_B_S_MCTS)   TimeTaken: 5.115 secs  -  Turn: 0  -  Time:17:44:30


In [70]:
def func_even(x): return abs(math.sin(2*math.pi*x))

player1 = MCTSPlayer(iterations=100, c_param = math.sqrt(2), name='MCTS1_sq2_100')
player2 = MCTSPlayer(iterations=100, c_param = math.sqrt(2), name='MCTS2_sq2_100')
state = FunctionOptimisationState(players=[player1, player2], function=func, ranges=[[0,1]], splits=2)

while (not state.isGameOver):
    if state.playerSymbol == 1:
        m = player1.chooseAction(state)
    else:
        m = player2.chooseAction(state)
    state.move(m)
    print(state)
print("result", state.result, " p:",state.function(state.eval_point()))

(MCTS1_sq2_100)   TimeTaken: 0.031 secs  -  Turn: 0  -  Time:15:03:24
([0.0, 0.5],)
([0.25, 0.5],)
([0.375, 0.5],)
([0.4375, 0.5],)
([0.4375, 0.46875],)
([0.453125, 0.46875],)
([0.453125, 0.4609375],)
([0.453125, 0.45703125],)
([0.453125, 0.455078125],)
([0.4541015625, 0.455078125],)
(MCTS1_sq2_100)   TimeTaken: 0.023 secs  -  Turn: 10  -  Time:15:03:24
([0.4541015625, 0.45458984375],)
([0.4541015625, 0.454345703125],)
([0.4541015625, 0.4542236328125],)
([0.45416259765625, 0.4542236328125],)
([0.45416259765625, 0.454193115234375],)
([0.4541778564453125, 0.454193115234375],)
([0.4541778564453125, 0.45418548583984375],)
result 0  p: 0.6672829459693022


In [21]:
x = np.linspace(0.001,1,5000)
y = [func4([i]) for i in x]
fig = go.Figure(data=go.Scatter(x=x, y=y))
fig.show()

In [31]:
player1 = RandomPlayer()
player2 = RandomPlayer()

state = CarcassonneState(player1, player2, no_monasteries = True, no_farms = True)
while (not state.isGameOver):
    
    if state.playerSymbol == 1:
        m = player1.chooseAction(state)
    else:
        m = player2.chooseAction(state) # make move

    state.move(m)
print(state.winner)

(Random)   TimeTaken: 0 secs  -  Turn: 10  -  Time:04:16:24
(Random)   TimeTaken: 0 secs  -  Turn: 20  -  Time:04:16:24
(Random)   TimeTaken: 0 secs  -  Turn: 30  -  Time:04:16:24
(Random)   TimeTaken: 0 secs  -  Turn: 40  -  Time:04:16:24
(Random)   TimeTaken: 0 secs  -  Turn: 50  -  Time:04:16:24
(Random)   TimeTaken: 0 secs  -  Turn: 60  -  Time:04:16:24
2


In [1]:
import os
import pandas as pd
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import numpy as np
import ast
import random
import math
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict

print(os.path.abspath(os.getcwd()))

logs_path = "logs"
exp_logs_names = ["Experiment_COMMA_WEAKS2022-01-07",
                    "Experiment_PLUS_WEAKS2022-01-03",
                    "Experiment_PLUS_WEAKS_REDUCED2022-01-10",
                    "Experiment_COMMA_WEAKS_REDUCED2022-01-11",
                    "Experiment_UL_SEM_C_2022-01-21",
                    "Experiment_UL_SEM_P_2022-01-20",
                    "4_EXP_All_Games"]

numbers = [str(x) for x in range(6)]
evostr_files = ["_ES_B_S_MCTS_EvoStr.csv", "_ES_B_MCTS_EvoStr.csv"]
join = "/"
uctstats = "UCTStats.csv"
semstats = "SemanticsStats.csv"

dfSSD = {}
uct_df = {}
holder = {}
sem_df = {}
for logs_name in exp_logs_names:
    dfSSD[logs_name] = pd.read_csv(logs_path + join + logs_name + join + "dfSSD.csv")
    uct_df[logs_name] = pd.read_csv(logs_path + join + logs_name + join + uctstats)
    sem_df[logs_name] = pd.read_csv(logs_path + join + logs_name + join + semstats)
    holder[logs_name] = {}
    for file in evostr_files:
        holder[logs_name][file] = {}
        for n in numbers:
            try:
                holder_filename = logs_path + join + logs_name + join + n + file
                holder[logs_name][file][n] = pd.read_csv(holder_filename)
            except:
                print(holder_filename, " was not found")
uct_df[exp_logs_names[0]].head()

d:\Users\fredx\Documents\Gits\mcts_uct_fred
logs/Experiment_PLUS_WEAKS_REDUCED2022-01-10/1_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/0_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/1_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/2_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/3_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/4_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/5_ES_B_S_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/0_ES_B_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/1_ES_B_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/2_ES_B_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/3_ES_B_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/4_ES_B_MCTS_EvoStr.csv  was not found
logs/Experiment_UL_SEM_C_2022-01-21/5_ES_B_MC

Name  Turn  Generation  Lambda  TotalNodes  AverageNodes  \
0  ES_B_S_MCTS     1           1       4          52          10.4   
1  ES_B_S_MCTS     1           2       4          78          15.6   
2  ES_B_S_MCTS     1           3       4          66          13.2   
3  ES_B_S_MCTS     1           4       4          64          12.8   
4  ES_B_S_MCTS     1           5       4          77          15.4   

   AverageDepth  AverageSSD  
0           4.4        5.75  
1           6.6        7.20  
2           4.6        7.55  
3           3.6        4.70  
4           3.4        9.05

In [2]:
by_turn = {}
for exp in exp_logs_names:
    df = uct_df[exp]
    averages = []
    stdevs = []
    max_turn = int(max(df["Turn"].values.tolist()))
    turns = list(range(1,max_turn+1))
    for turn in turns:
        list_values = df.loc[df["Turn"]==turn,["AverageSSD"]].values.tolist()
        average = np.average(list_values)
        stdev = np.std(list_values)
        averages.append(average)
        stdevs.append(stdev)
    data = {"Turn":turns, "AverageSSD":averages, "StdevSSD":stdevs}
    by_turn[exp] = pd.DataFrame(data)

    #print(by_turn[exp].head())

In [ ]:
by_gen = {}
for exp in exp_logs_names:
    df = uct_df[exp]
    averages = []
    stdevs = []
    max_gen = int(max(df["Generation"].values.tolist()))
    gens = list(range(1,max_gen+1))
    for gen in gens:
        list_values = df.loc[df["Generation"]==gen,["AverageSSD"]].values.tolist()
        average = np.average(list_values)
        stdev = np.std(list_values)
        averages.append(average)
        stdevs.append(stdev)
    data = {"Generation":gens, "AverageSSD":averages, "StdevSSD":stdevs}
    by_gen[exp] = pd.DataFrame(data)

    #print(by_gen[exp].head())

In [ ]:
import matplotlib.pyplot as plt

SSD_by_turn = {}
for exp in exp_logs_names:
    fig, ax = plt.subplots(figsize=(10,5))
    SSD_by_turn[exp] = dfSSD[exp].boxplot(ax=ax, column = "SSD", by = "Turn", figsize=(10,5), return_type='axes')
    ax.set_ylim([0,20])


In [ ]:
uct_df_siea = {}
uct_df_ea = {}
for exp in exp_logs_names:
    uct_df_siea[exp] = uct_df[exp].loc[uct_df[exp]["Name"]=="ES_B_S_MCTS"]
    uct_df_ea[exp] = uct_df[exp].loc[uct_df[exp]["Name"]=="ES_B_MCTS"]

    fig, ax = plt.subplots(figsize=(10,5))
    SSD_by_gen = uct_df_siea[exp].boxplot(ax=ax, column = "AverageSSD", by = "Generation", figsize=(10,5), return_type='axes')
    ax.set_ylim([0,20])
    
    ax.set_title("SIEA_MCTS SSD by Generation : " + exp)

    fig, ax = plt.subplots(figsize=(10,5))
    SSD_by_gen = uct_df_ea[exp].boxplot(ax=ax, column = "AverageSSD", by = "Generation", figsize=(10,5), return_type='axes')
    ax.set_ylim([0,20])
    
    ax.set_title("EA_MCTS SSD by Generation : " +  exp)


In [2]:
def check_ratio(L,U,return_as="Decisive_by_turn",experiments_with=None): 
    total = 0
    decisive_count = 0
    min_count = 0
    decisive_by_turn = defaultdict(lambda: 0)
    min_by_turn = defaultdict(lambda: 0)
    not_random_by_turn = defaultdict(lambda: 0)
    total_by_turn = defaultdict(lambda: 0)
    relevant_ssds_turn = defaultdict(lambda: [])
    ssds = []

    if experiments_with is not None:
        exps = [exp for exp in exp_logs_names if experiments_with in exp]
    else:
        exps = exp_logs_names
        
    for exp in exps:
        df = sem_df[exp]
        for index, row in df.iterrows():
            fitnesses = row.Fitnesses
            semantics = row.SSDs
            fitnesses = fitnesses.replace(",","")
            fitnesses = fitnesses.replace("(","")
            fitnesses = fitnesses.replace("[","")
            semantics = semantics.replace("[","")
            fitnesses = fitnesses.replace("]","")
            semantics = semantics.replace("]","")
            fitnesses = fitnesses.replace(",","")
            fitnesses = fitnesses[:-1]
            fitnesses = fitnesses.split(")")
            semantics = semantics.split(",")
            fitnesses = [float(f) for f in fitnesses]
            semantics = [float(f) for f in semantics]
            max_fitness = max(fitnesses[1:])
            max_indexes = [i for i,v in enumerate(fitnesses) if float(v) == max_fitness]
            filtered_semantics = [s for i,s in enumerate(semantics) if i in max_indexes]
            relevant_ssds_turn[row.Turn] += filtered_semantics
            in_range = [s for s in filtered_semantics if s < U and s > L]
            ssds += in_range
            if len(in_range) == 1: 
                decisive_count += 1
                decisive_by_turn[row.Turn] += 1
                not_random_by_turn[row.Turn] += 1
            if len(in_range) > 1: 
                min_count += 1
                min_by_turn[row.Turn] += 1
                not_random_by_turn[row.Turn] += 1
            total += 1
            total_by_turn[row.Turn] += 1


    """ Info zone
    print("stdev",stats.stdev(ssds))
    print("mean",stats.mean(ssds))
    print("quantiles",np.quantile(ssds, q = np.arange(0.25, 1, 0.25))) 
    fig = plt.figure(figsize =(10, 7))
    plt.boxplot(ssds)
    plt.show()
    """
    if return_as == "Decisive_by_turn":
        turn_ratios = []
        for turn, value in total_by_turn.items():
            turn_ratios.append(decisive_by_turn[turn]/value)   
        return stats.mean(turn_ratios)

    if return_as == "Decisive":
        return decisive_count/total

    if return_as == "Min":
        return min_count/total

In [107]:
print(check_ratio(0,50))

0.4471804646285321


In [8]:
step_size = 1
min_step_size = 0.001

L = 0
U = 20
best_L = L
best_U = U
best_ratio = 0
L_turn = True

while step_size > min_step_size:
    
    ratio = check_ratio(L,U, experiments_with="All")
    #ratio = check_ratio(L,U, "Decisive")
    if ratio >= best_ratio: 
        best_ratio = ratio
        best_L = L
        best_U = U
        print("New best! L: ",L, " U: ", U, " Ratio: ", ratio)
    
        if L_turn:
            L += step_size
        else:
            U -= step_size
    
    
    else:
        if L_turn:
            L -= step_size
            L_turn = False
        else:
            U += step_size
            L_turn = True
            step_size = step_size/10

    

New best! L:  0  U:  20  Ratio:  0.7794219447424455
New best! L:  0  U:  20  Ratio:  0.7794219447424455
New best! L:  0  U:  19  Ratio:  0.7794219447424455
New best! L:  0  U:  18  Ratio:  0.7794219447424455
New best! L:  0  U:  17  Ratio:  0.7794219447424455
New best! L:  0  U:  16  Ratio:  0.7794219447424455
New best! L:  0  U:  15  Ratio:  0.7794219447424455
New best! L:  0  U:  14  Ratio:  0.7794219447424455
New best! L:  0  U:  13  Ratio:  0.7794219447424455
New best! L:  0  U:  12  Ratio:  0.7794219447424455
New best! L:  0  U:  11  Ratio:  0.7794219447424455
New best! L:  0  U:  10  Ratio:  0.7794219447424455
New best! L:  0  U:  9  Ratio:  0.7794219447424455
New best! L:  0  U:  8  Ratio:  0.7794219447424455
New best! L:  0  U:  7  Ratio:  0.7799666070518138
New best! L:  0  U:  7  Ratio:  0.7799666070518138
New best! L:  0.0  U:  7  Ratio:  0.7799666070518138
New best! L:  0.0  U:  7.0  Ratio:  0.7799666070518138
New best! L:  0.01  U:  7.0  Ratio:  0.7799666070518138
New best

In [3]:
import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
  
#UCTStats:
#Name	Turn	Generation	Lambda	TotalNodes	AverageNodes	AverageDepth	AverageSSD	IsFirstPlayer	Opponent

#Plot options:
#https://plotly.com/python/creating-and-updating-figures/
#https://pythonwife.com/bar-charts-with-plotly/

print(os.path.abspath(os.getcwd()))

logs_path = "logs"
join = "/"
uctstats = "UCTStats.csv"
semstats = "SemanticsStats.csv"
prom_exps = ["Experiment_UL_SEM_C_2022-01-30",
            "Experiment_UL_SEM_P_2022-01-20"]
prev_exps =  ["Experiment_S2_WEAKS2022-01-31",
            "Experiment_PLUS_WEAKS2022-01-03",
            "Experiment_PLUS_WEAKS_REDUCED2022-01-10",
            "Experiment_COMMA_WEAKS_REDUCED2022-01-11"]
L = 0.39
U = 8.34



def get_players(exp_name):
    league_table = pd.read_csv(logs_path + join + exp_name + join + "FinalLeagueTable.csv")
    players = league_table["Player"].to_list()
    return players

def get_range(df_fitnesses, df_semantics, L, U, comma=False):
    ranges = []
    for index, fitnesses in enumerate(df_fitnesses):
        semantics = df_semantics.iloc[index]
        fitnesses = fitnesses.replace(",","")
        fitnesses = fitnesses.replace("(","")
        fitnesses = fitnesses.replace("[","")
        semantics = semantics.replace("[","")
        fitnesses = fitnesses.replace("]","")
        semantics = semantics.replace("]","")
        fitnesses = fitnesses.replace(",","")
        fitnesses = fitnesses[:-1]
        fitnesses = fitnesses.split(")")
        semantics = semantics.split(",")
        fitnesses = [float(f) for f in fitnesses]
        semantics = [float(f) for f in semantics]
        max_fitness = max(fitnesses[1:])
        if comma:
            max_indexes = [i for i,v in enumerate(fitnesses) if float(v) == max_fitness and i!=0]
        else:
            max_indexes = [i for i,v in enumerate(fitnesses) if float(v) == max_fitness]
        filtered_semantics = [s for i,s in enumerate(semantics) if i in max_indexes]
        in_range = [s for s in filtered_semantics if s < U and s > L]
        ranges.append(len(in_range))
    return ranges

def define_tiebreak(fitnesses, semantics, L, U, comma=False):
    tiebreaks = []
    ranges = get_range(fitnesses, semantics, L, U, comma)
    #print(ranges)
    for n_in_range in ranges:
        if n_in_range == 1: tiebreaks.append("Decisive")
        elif n_in_range >= 2: tiebreaks.append("Minimum")
        else: tiebreaks.append("Random")
    return tiebreaks

def semantics_stats_analysis(exp_name, L, U, plot_random_by_turn=True, plot_ssd_by_turn=True, plot_equals_by_turn=True, comma=False):
    all = {}

    #get needed variables
    games_data = pd.read_csv(logs_path + join + exp_name + join + "GamesCompleted.csv")
    n_games = games_data.Total_Games[0]
    
    #Semantics stats
    stats = pd.read_csv(logs_path + join + exp_name + join + "SemanticsStats.csv")
    equal_fitnesses = len(stats)

    #Semantics stats
    uct_stats = pd.read_csv(logs_path + join + exp_name + join + "UCTStats.csv")

    #Formulas stats
    formulas = pd.read_csv(logs_path + join + exp_name + join + "EvolvedUCT.csv")

    #Calculate decisives and minimums
    stats = stats.assign(tiebreak=lambda x: define_tiebreak(x.Fitnesses, x.SSDs, L, U, comma))
    stats = stats.assign(decisive=lambda x: x.tiebreak=="Decisive")
    stats = stats.assign(minimum=lambda x: x.tiebreak=="Minimum")

    #Grouped by turn
    uct_stats_by_turn = uct_stats.groupby(["Turn"]).mean()
    stats_by_turn = stats.groupby(["Turn"]).mean()

    #assignation
    all["n_games"] = n_games
    all["equal_fitnesses"] = equal_fitnesses
    all["equal_fitnesses_by_game"] = equal_fitnesses/n_games
    all["randoms"] = stats.WasRandom.mean()
    all["stats"] = stats
    all["uct_stats_by_turn"] = uct_stats_by_turn
    all["stats_by_turn"] = stats_by_turn
    all["formulas"] = formulas

    return all





d:\Users\fredx\Documents\Gits\mcts_uct_fred


In [33]:

sem_stats = semantics_stats_analysis(prom_exps[0],L,U,comma=True)
sem_stats_p = semantics_stats_analysis(prom_exps[1],L,U)

old_sem_stats = semantics_stats_analysis(prev_exps[0],L=5,U=10, comma=True)
old_sem_stats_p = semantics_stats_analysis(prev_exps[1],L=5,U=10)


###########Tiebreak distribution
exps_data = [sem_stats["stats"], sem_stats_p["stats"], old_sem_stats["stats"], old_sem_stats_p["stats"]]
exps_names = ["Comma_PS", "Plus_PS", "Comma", "Plus"]
tiebreaks = ["Random","Decisive","Minimum"]
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}



plot = make_subplots(rows=2, cols=3
    , shared_yaxes=True
    , subplot_titles=("Full experiment", "Without turn 36", "With turns up to 33")
    , x_title="Data included"
)
legend_not_added = True
for t in tiebreaks:
    y = [len(df[df["tiebreak"]==t])/len(df) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=legend_not_added
        ,marker={'color': colors[t]}
        )
    ,row=1
    ,col=1
    )

    y = [len(df[df["tiebreak"]==t][df["Turn"]!=36])/len(df[df["Turn"]!=36]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=False
        ,marker={'color': colors[t]}
        )
    ,row=1
    ,col=2
    )

    y = [len(df[df["tiebreak"]==t][df["Turn"]<34])/len(df[df["Turn"]<34]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=False
        ,marker={'color': colors[t]}
        )
    ,row=1
    ,col=3
    )
    
for t in tiebreaks:
    y = [len(df[df["tiebreak"]==t]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=legend_not_added
        ,marker={'color': colors[t]}
        )
    ,row=2
    ,col=1
    )

    y = [len(df[df["tiebreak"]==t][df["Turn"]!=36]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=False
        ,marker={'color': colors[t]}
        )
    ,row=2
    ,col=2
    )

    y = [len(df[df["tiebreak"]==t][df["Turn"]<34]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y,
        showlegend=False
        ,marker={'color': colors[t]}
        )
    ,row=2
    ,col=3
    )
    
plot.update_layout(barmode='stack'
            ,title="Tiebreak count and distribution"
            #,xaxis_title="Experiment"
            #,yaxis_title="Count"
            ,legend_title="Tiebreak")
plot["layout"]["yaxis1"]["title"] = "Distribution"
plot["layout"]["yaxis4"]["title"] = "Count"
#plot.update_xaxes(showgrid=True, gridwidth=1)        
plot.show()




###########Tiebreak count
plot = go.Figure()
for t in tiebreaks:
    y = [len(df[df["tiebreak"]==t]) for df in exps_data]
    plot.add_trace(go.Bar(
        name = t,
        x = exps_names,
        y=y
    ))
plot.update_layout(barmode='stack'
            ,title="Tiebreak total if equal fitness"
            ,xaxis_title="Experiment"
            ,yaxis_title="Amount"
            ,legend_title="Tiebreak")              
plot.show()





###########Tiebreak by turn
legend_not_added = True
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    , row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    x = full_df["Turn"].unique()
    for t in tiebreaks:
        y=[]
        for turn in x:
            df = full_df[full_df["Turn"]==turn]
            y.append(len(df[df["tiebreak"]==t])/len(df))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=legend_not_added
                ),
            row = row+1,
            col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak distribution by turn"
            ,xaxis_title="Turn"
            ,yaxis_title="Proportion"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()


legend_not_added = True
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    x = full_df["Turn"].unique()
    for t in tiebreaks:
        y=[]
        for turn in x:
            df = full_df[full_df["Turn"]==turn]
            y.append(len(df[df["tiebreak"]==t]))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=legend_not_added
                ),
            row = row+1,
            col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak count by turn"
            ,xaxis_title="Turn"
            ,yaxis_title="Count"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()

legend_not_added = True
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    x = full_df["Turn"].unique()
    for t in tiebreaks:
        y=[]
        for turn in x:
            df = full_df[full_df["Turn"]==turn]
            y.append(len(df[df["tiebreak"]==t]))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=legend_not_added
                ),
            row = row+1,
            col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak count by turn"
            ,xaxis_title="Turn"
            ,yaxis_title="Count"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()





colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
     x = full_df["Generation"].unique()
     for t in tiebreaks:
        y=[]
        for gen in x:
            df = full_df[full_df["Generation"]==gen][full_df["Turn"]<=34]
            y.append(len(df[df["tiebreak"]==t]))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                #showlegend=False),
                ),
            row = row+1,
            col = 1)
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak count by generation with turns up to 33"
            ,xaxis_title="Generation"
            ,yaxis_title="Count"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()

#missing: correlation between average nodes and ssd by generation


C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\3485118013.py:37: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\3485118013.py:49: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\3485118013.py:74: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\3485118013.py:86: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\3485118013.py:260: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



In [22]:
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}

sem_stats = semantics_stats_analysis(prom_exps[0],L,U,comma=True)
sem_stats_p = semantics_stats_analysis(prom_exps[1],L,U)
#old_sem_stats = semantics_stats_analysis(prev_exps[0],L,U, comma=True)
#old_sem_stats_p = semantics_stats_analysis(prev_exps[1],L,U)

exps_data = [sem_stats["stats"], sem_stats_p["stats"]]#, old_sem_stats["stats"], old_sem_stats_p["stats"]]
exps_names = ["Comma_PS", "Plus_PS"]#, "Comma", "Plus"]
tiebreaks = ["Random","Decisive","Minimum"]


plot = make_subplots(rows=2, cols=2
    , shared_yaxes=True
    , subplot_titles=(exps_names + [n + " excluding turn 36" for n in exps_names])
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True
    , x_title="Is first player?"
    , y_title="Count"
    )
leyend_needed = True

for col, full_df in enumerate(exps_data):

    x = full_df["IsFirstPlayer"].unique()
    for t in tiebreaks:
        y=[]
        y2 = []
        for p in x:
            df = full_df[full_df["IsFirstPlayer"]==p]
            df2 = full_df[full_df["IsFirstPlayer"]==p][full_df["Turn"]!=36]
            #df = full_df.loc[((full_df['IsFirstPlayer'] == p) & (full_df['Turn'] == 36))]
            y.append(len(df[df["tiebreak"]==t]))
            y2.append(len(df2[df2["tiebreak"]==t]))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=leyend_needed
                ),
            row = 1,
            col = 1+col)
        plot.add_trace(go.Bar(
                name=t,x=x,y=y2
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=False
                ),
            row = 2,
            col = 1+col)
    leyend_needed = False
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak count when first or second player"
            #,xaxis_title="Is first player?"
            #,yaxis_title="Count"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=400)  
#plot['layout']['xaxis2']['title']="Is first player?"                
plot.show()
##Note: first player gets an extra turn



plot = make_subplots(rows=1, cols=2
    , shared_yaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for col, full_df in enumerate(exps_data):
     x = full_df["IsFirstPlayer"].unique()
     for t in tiebreaks:
        y=[]
        for p in x:
            df = full_df[full_df["IsFirstPlayer"]==p]
            y.append(len(df[df["tiebreak"]==t])/len(df))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                #showlegend=False),
                ),
            row = 1,
            col = 1+col)
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak distribution when first or second player"
            ,xaxis_title="Is first player?"
            ,yaxis_title="Proportion"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=400)                
plot.show()

This is the format of your plot grid:
[ (1,1) x,y   ]  [ (1,2) x2,y2 ]
[ (2,1) x3,y3 ]  [ (2,2) x4,y4 ]



C:\Users\Fredasus\AppData\Local\Temp\ipykernel_9840\2966795233.py:34: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



This is the format of your plot grid:
[ (1,1) x,y   ]  [ (1,2) x2,y2 ]



In [45]:
colors = {'Random': 'red',
          'Minimum': 'orange',
          'Decisive': 'lightgreen'}

sem_stats = semantics_stats_analysis(prom_exps[0],L,U,comma=True)
sem_stats_p = semantics_stats_analysis(prom_exps[1],L,U)
#old_sem_stats = semantics_stats_analysis(prev_exps[0],L,U, comma=True)
#old_sem_stats_p = semantics_stats_analysis(prev_exps[1],L,U)

exps_data = [sem_stats["stats"], sem_stats_p["stats"]]#, old_sem_stats["stats"], old_sem_stats_p["stats"]]
exps_names = ["Comma_PS", "Plus_PS"]#, "Comma", "Plus"]
tiebreaks = ["Random","Decisive","Minimum"]


plot = make_subplots(rows=1, cols=2
    , shared_yaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for col, full_df in enumerate(exps_data):
     x = full_df["Opponent"].unique()
     for t in tiebreaks:
        y=[]
        for p in x:
            df = full_df[full_df["Opponent"]==p]
            y.append(len(df[df["tiebreak"]==t]))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                #showlegend=False),
                ),
            row = 1,
            col = 1+col)
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak count by opponent"
            ,xaxis_title="Opponent"
            ,yaxis_title="Count"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=400)                
plot.show()
##Note: first player gets an extra turn

plot = make_subplots(rows=1, cols=2
    , shared_yaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for col, full_df in enumerate(exps_data):
     x = full_df["Opponent"].unique()
     for t in tiebreaks:
        y=[]
        for p in x:
            df = full_df[full_df["Opponent"]==p]
            y.append(len(df[df["tiebreak"]==t])/len(df))
        plot.add_trace(go.Bar(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                #showlegend=False),
                ),
            row = 1,
            col = 1+col)
plot.update_layout(barmode='stack'
            ,title_text="Tiebreak distribution by opponent"
            ,xaxis_title="Opponent"
            ,yaxis_title="Proportion"
            ,legend_title="Tiebreak"
            ,autosize=False
            ,width=1000
            ,height=400)                
plot.show()

This is the format of your plot grid:
[ (1,1) x,y   ]  [ (1,2) x2,y2 ]



This is the format of your plot grid:
[ (1,1) x,y   ]  [ (1,2) x2,y2 ]



In [38]:

sem_stats = semantics_stats_analysis(prom_exps[0],L,U,comma=True)
sem_stats_p = semantics_stats_analysis(prom_exps[1],L,U)
#old_sem_stats = semantics_stats_analysis(prev_exps[0],L,U, comma=True)
#old_sem_stats_p = semantics_stats_analysis(prev_exps[1],L,U)

exps_data = [sem_stats["stats"], sem_stats_p["stats"]]#, old_sem_stats["stats"], old_sem_stats_p["stats"]]
exps_names = ["Comma_PS", "Plus_PS"]#, "Comma", "Plus"]
tiebreaks = ["Random","Decisive","Minimum"]

full_df = exps_data[1]

plot = go.Figure()
x = full_df["Generation"].unique()
y=[]
for p in x:
    df = full_df[full_df["Generation"]==p]
    y.append(len(df[df["BestIndex"]==0])/len(df))
plot.add_trace(go.Bar(
        name=t,x=x,y=y
        ))
plot.update_layout(barmode='stack'
            ,title_text="Plus: Rate of parent kept as winner"
            ,xaxis_title="Generation"
            ,yaxis_title="Rate"
            ,autosize=False
            ,width=500
            ,height=400)                
plot.show()

In [5]:
##Formulas

import statistics as stats

sem_stats = semantics_stats_analysis(prom_exps[0],L,U,comma=True)
sem_stats_p = semantics_stats_analysis(prom_exps[1],L,U)
old_sem_stats = semantics_stats_analysis(prev_exps[0],5,10, comma=True)
old_sem_stats_p = semantics_stats_analysis(prev_exps[1],5,10 )

exps_data = [sem_stats["formulas"], sem_stats_p["formulas"], old_sem_stats["formulas"], old_sem_stats_p["formulas"]]
exps_names = ["Comma_PS", "Plus_PS", "Comma", "Plus"]

terminals = ["Q","N","n"]

legend_not_added = True
colors = {'Q': 'red',
          'N': 'orange',
          'n': 'lightgreen'}
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    x = full_df["Turn"].unique()
    for t in terminals:
        y=[]
        for turn in x:
            df = full_df[full_df["Turn"]==turn]
            #print("test len",df["Function"])
            y.append(len(df[df["Function"].str.contains(t)]))
        plot.add_trace(go.Scatter(
                name=t,x=x,y=y
                ,legendgroup='group1'
                ,marker={'color': colors[t]}
                ,showlegend=legend_not_added
                ,mode='lines+markers'
                ),
            row = row+1,
            col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(#barmode='group'
            #,
            title_text="Terminal appearence count by turn"
            ,xaxis_title="Turn"
            ,yaxis_title="Count"
            ,legend_title="Terminal"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()



legend_not_added = True
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    full_df = full_df[full_df["IsDifferent"]]
    x = full_df["Turn"]
    y = full_df["NumberNodes"]
    plot.add_trace(go.Box(
        name="Number of Nodes",x=x,y=y
        ,legendgroup='group1'
        ,showlegend=legend_not_added
        ),
    row = row+1,
    col = 1)
    plot.add_trace(go.Scatter(x=x, y=[13 for _ in x],
                    mode='lines',legendgroup='group1'
                    ,showlegend=legend_not_added,
                    name='original UCT'),
    row = row+1,
    col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(title_text="Number of nodes in the formula by turn (if different from original)"
            ,xaxis_title="Turn"
            ,yaxis_title="Value"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()

legend_not_added = True
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    full_df = full_df[full_df["IsDifferent"]]
    x = full_df["Turn"]
    y = full_df["Depth"]
    plot.add_trace(go.Box(
        name="Depth",x=x,y=y
        ,legendgroup='group1'
        ,showlegend=legend_not_added
        ),
    row = row+1,
    col = 1)
    plot.add_trace(go.Scatter(x=x, y=[6 for _ in x],
                    mode='lines',legendgroup='group1'
                    ,showlegend=legend_not_added,
                    name='original UCT'),
    row = row+1,
    col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(title_text="Depth of the formula tree by turn (if different from original)"
            ,xaxis_title="Turn"
            ,yaxis_title="Value"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()


legend_not_added = True
plot = make_subplots(rows=4, cols=1
    , shared_xaxes=True
    , subplot_titles=(exps_names)
    #, row_heights=[4 for _ in exps_names]
    #, vertical_spacing=0.3
    , print_grid=True)
for row, full_df in enumerate(exps_data):
    x = full_df["Turn"].unique()
    y=[]
    strings = []
    for turn in x:
        df = full_df[full_df["Turn"]==turn]
        ratio = stats.mean(df["IsDifferent"])
        y.append(ratio)
        strings.append(str(ratio))
    plot.add_trace(go.Scatter(
            name=t,x=x,y=y,text=strings
            ,legendgroup='group1'
            ,showlegend=legend_not_added
            ,mode='lines+markers'
            ),
        row = row+1,
        col = 1)
    if legend_not_added:
        legend_not_added = False
plot.update_layout(
            #barmode='group'
            #,
            title_text="Formula changed by turn"
            ,xaxis_title="Turn"
            ,yaxis_title="Ratio"
            ,autosize=False
            ,width=1000
            ,height=800)                
plot.show()

This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]
[ (4,1) x4,y4 ]



In [27]:
import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp

print(os.path.abspath(os.getcwd()))

logs_path = "logs"
join = "/"

def scores_analysis(exp_name, join=join, logs_path=logs_path, plot_show=[True, True, True]):

    scores_data = pd.read_csv(logs_path + join + exp_name + join + "PlayerStats.csv")
    agents = scores_data["Player"].unique()
    n_agents = len(agents)
    print(agents)
    all_colors = ["blue","orange","green","yellow","red","black","pink","brown","purple","gray" ]
    assert(n_agents <= len(all_colors))
    colors = {opponent:all_colors[i] for i,opponent in enumerate(agents)}

    for agent in agents:
        featured = []
        for i, row in scores_data.iterrows():
            featured.append(row["Opponent"]==agent or row["Player"]==agent)
        scores_data["featured_"+agent] = featured

    ############ Score distribution as first

    if plot_show[0]==True:
        plot = make_subplots(rows=3, cols=1
            #,shared_xaxes=True
            #,shared_yaxes=True
            ,subplot_titles=["Score by opponent","Score difference by opponent","Score proportion by opponent"]
            #,row_heights=[4 for _ in exps_names]
            #,vertical_spacing=0.3
            ,print_grid=True
            ,x_title="Player")

        for i,opponent in enumerate(agents):
            
            filtered_data = scores_data[scores_data["Opponent"]==opponent]
            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=True),
                row = 1,
                col = 1)

            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"]-filtered_data["OpponentScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=False),
                row = 2,
                col = 1)

            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"]/filtered_data["OpponentScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=False),
                row = 3,
                col = 1)

        plot.update_layout(
            boxmode='group'
            ,title_text="Score distribution as first player"
            #,xaxis_title="Player"
            ,yaxis_title="Score"
            ,legend_title="Opponent"
            ,autosize=False
            ,width=1300
            ,height=1200)
            
        plot.show()

    ############ Score distribution as second

    if plot_show[1]==True:
        plot = make_subplots(rows=3, cols=1
            #,shared_xaxes=True
            #,shared_yaxes=True
            ,subplot_titles=["Score by opponent","Score difference by opponent","Score proportion by opponent"]
            #,row_heights=[4 for _ in exps_names]
            #,vertical_spacing=0.3
            ,print_grid=True
            ,x_title="Player")

        for i,opponent in enumerate(agents):
            
            filtered_data = scores_data[scores_data["Opponent"]==opponent]
            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=True),
                row = 1,
                col = 1)

            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"]-filtered_data["OpponentScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=False),
                row = 2,
                col = 1)

            plot.add_trace(
                go.Box(
                    y=filtered_data["PlayerScore"]/filtered_data["OpponentScore"],
                    x=filtered_data["Player"],
                    name=opponent,
                    marker_color=colors[opponent],
                    showlegend=False),
                row = 3,
                col = 1)

        plot.update_layout(
            boxmode='group'
            ,title_text="Score distribution as second player"
            #,xaxis_title="Player"
            ,yaxis_title="Score"
            ,legend_title="Opponent"
            ,autosize=False
            ,width=1300
            ,height=1200)
            
        plot.show()

    ####### Opponent's scores

    if plot_show[2]==True:
        plot = make_subplots(rows=3, cols=2
            #,shared_xaxes=True
            #,shared_yaxes=True
            ,subplot_titles=["Opponent's combined score","Opponent's combined score difference","Opponent's combined score proportion"]
            #,row_heights=[4 for _ in exps_names]
            #,vertical_spacing=0.3
            ,print_grid=True
            ,x_title="Player")
        

        plot.add_trace(
                go.Box(
                    y=scores_data["OpponentScore"],
                    x=scores_data["Player"],
                    name="As 1st",
                    legendgroup='group1',
                    #marker_color=colors[opponent],
                    showlegend=True),
                row = 1,
                col = 1)

        plot.add_trace(
                go.Box(
                    y=scores_data["PlayerScore"]-scores_data["OpponentScore"],
                    x=scores_data["Player"],
                    legendgroup='group1',
                    #name=opponent,
                    #marker_color=colors[opponent],
                    showlegend=False),
                row = 2,
                col = 1)

        plot.add_trace(
                go.Box(
                    y=scores_data["PlayerScore"]/scores_data["OpponentScore"],
                    x=scores_data["Player"],
                    legendgroup='group1',
                    #name=opponent,
                    #marker_color=colors[opponent],
                    showlegend=False),
                row = 3,
                col = 1)

        plot.add_trace(
                go.Box(
                    y=scores_data["PlayerScore"],
                    x=scores_data["Opponent"],
                    name="As 2nd",
                    legendgroup='group2',
                    #marker_color=colors[opponent],
                    showlegend=True),
                row = 1,
                col = 2)

        plot.add_trace(
                go.Box(
                    y=scores_data["OpponentScore"]-scores_data["PlayerScore"],
                    x=scores_data["Opponent"],
                    legendgroup='group2',
                    #name=opponent,
                    #marker_color=colors[opponent],
                    showlegend=False),
                row = 2,
                col = 2)

        plot.add_trace(
                go.Box(
                    y=scores_data["OpponentScore"]/scores_data["PlayerScore"],
                    x=scores_data["Opponent"],
                    legendgroup='group2',
                    #name=opponent,
                    #marker_color=colors[opponent],
                    showlegend=False),
                row = 3,
                col = 2)

        plot.update_layout(
            boxmode='group'
            ,title_text="Score distribution"
            #,xaxis_title="Player"
            ,yaxis_title="Score"
            ,legend_title="Player"
            ,autosize=False
            ,width=1300
            ,height=800)
            
        plot.show()

    return scores_data, agents


d:\Users\fredx\Documents\Gits\mcts_uct_fred


In [26]:
scores_data, agents = scores_analysis("4_EXP_All_Games", join=join, logs_path=logs_path)
stats_dict = {}
stats_dict["difference"] = {}
stats_dict["scores"] = {}
stats_dict["opponent_scores"] = {}

for player in agents:
   for opponent in agents:
      tempa = scores_data[scores_data["Player"]==player]
      tempb = scores_data[scores_data["Player"]==opponent]
      a = tempa["PlayerScore"]-tempa["OpponentScore"]
      b = tempb["PlayerScore"]-tempa["OpponentScore"]
      stats_dict("")
      tStat, pValue = stats.ttest_ind(a, b, equal_var = False) #run independent sample T-Test
      print("P-Value:{0} T-Statistic:{1}".format(pValue,tStat))

#t-test

['MCTS_2' 'Star1' 'ES_B_S_MCTS' 'ES_B_MCTS' 'M_RAVE_0.25' 'M_RAVE_0.5'
 'MCTS_1' 'Random' 'ES_MCTS']
This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]



This is the format of your plot grid:
[ (1,1) x,y   ]
[ (2,1) x2,y2 ]
[ (3,1) x3,y3 ]



This is the format of your plot grid:
[ (1,1) x,y   ]  [ (1,2) x2,y2 ]
[ (2,1) x3,y3 ]  [ (2,2) x4,y4 ]
[ (3,1) x5,y5 ]  [ (3,2) x6,y6 ]



In [80]:
#t-test: https://www.hackdeploy.com/python-t-test-a-friendly-guide/

import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp
from scipy import stats as spst
from datetime import date


print(os.path.abspath(os.getcwd()))

logs_path = "logs"
join = "/"
exp = "1_EXP_MCTS_Param"

def significance_test_allvsall(exp_name, threshold = 0.05):
   data =  pd.read_csv(logs_path + join + exp_name + join + "PlayerStats.csv")
   first = True
   lista = []
   for _ in range(len(data)):
      lista.append(first)
      if first: first = False
      else: first = True
   data["IsFirstPlayer"] = lista

   agents = data["Player"].unique()
   print("Agents: ", agents)

   ##Difference
   pvals = {}
   sig_dict = {}
   ##Scores
   s_pvals = {}
   s_sig_dict = {}
   ##2Scores
   s2_pvals = {}
   s2_sig_dict = {}
   checked_players = []
   filtered_data = data[data["IsFirstPlayer"]==True]
   #filtered_data = data
   for player in agents:
      player_significants = []
      player_pvals = []
      s_player_significants = []
      s_player_pvals = []
      s2_player_significants = []
      s2_player_pvals = []
      for opponent in agents:

         if player != opponent:
            filtered_data_a = filtered_data[filtered_data["Player"]==player]
            data_a = filtered_data_a[filtered_data_a["Opponent"]==opponent]
            a = data_a["PlayerScore"]-data_a["OpponentScore"]
            s2_a = data_a["OpponentScore"]
            s_a = data_a["PlayerScore"]

            filtered_data_b = filtered_data[filtered_data["Player"]==opponent]
            data_b = filtered_data_b[filtered_data_b["Opponent"]==player]
            b = data_b["PlayerScore"]-data_b["OpponentScore"]
            s2_b = data_b["OpponentScore"]
            s_b = data_b["PlayerScore"]
            
            tStat, pValue = spst.ttest_ind(a, b, equal_var = False)
            player_significants.append(pValue<threshold)
            player_pvals.append(pValue)
            #print("1:",player,", 2:",opponent," ,pval: ",pValue)

            s_tStat, s_pValue = spst.ttest_ind(s_a, s_b, equal_var = False)
            s_player_significants.append(s_pValue<threshold)
            s_player_pvals.append(s_pValue)

            s2_tStat, s2_pValue = spst.ttest_ind(s2_a, s2_b, equal_var = False)
            s2_player_significants.append(s2_pValue<threshold)
            s2_player_pvals.append(s2_pValue)

         else:
            player_significants.append(None)
            player_pvals.append(None)
            s_player_significants.append(None)
            s_player_pvals.append(None)
            s2_player_significants.append(None)
            s2_player_pvals.append(None)

      checked_players.append(player)

      sig_dict[player] = player_significants
      pvals[player] = player_pvals
      s_sig_dict[player] = s_player_significants
      s_pvals[player] = s_player_pvals
      s2_sig_dict[player] = s2_player_significants
      s2_pvals[player] = s2_player_pvals
   
   sig_data = pd.DataFrame(sig_dict, index=agents)
   pvals_data = pd.DataFrame(pvals, index=agents).round(5)
   s_sig_data = pd.DataFrame(s_sig_dict, index=agents)
   s_pvals_data = pd.DataFrame(s_pvals, index=agents).round(5)
   s2_sig_data = pd.DataFrame(s2_sig_dict, index=agents)
   s2_pvals_data = pd.DataFrame(s2_pvals, index=agents).round(5)

   today = date.today()
   d = today.strftime("_%d_%m_%Y_%H_%M_%S")

   sig_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_diff_significance"+ d+".csv")
   pvals_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_diff_pvalues"+ d+".csv")
   s_sig_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score_significance"+ d+".csv")
   s_pvals_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score_pvalues"+ d+".csv")
   s2_sig_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score2_significance"+ d+".csv")
   s2_pvals_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score2_pvalues"+ d+".csv")
      
   return pvals_data, s_pvals_data, s2_pvals_data

#pvals_data, s_pvals_data, s2_pvals_data = significance_test_allvsall(exp)
pvals_data, s_pvals_data, s2_pvals_data = significance_test_allvsall("2_EXP_RAVE_Param")
print(pvals_data)
print(s_pvals_data)
print(s2_pvals_data)


         




d:\Users\fredx\Documents\Gits\mcts_uct_fred
Agents:  ['M_RAVE_0.5' 'M_RAVE_3' 'M_RAVE_2' 'M_RAVE_1' 'M_RAVE_0.25'
 'Add_M_RAVE_sqrt2']
                  M_RAVE_0.5  M_RAVE_3  M_RAVE_2  M_RAVE_1  M_RAVE_0.25  \
M_RAVE_0.5               NaN   0.00000   0.00000   0.00002      0.22330   
M_RAVE_3             0.00000       NaN   0.00002   0.00000      0.00000   
M_RAVE_2             0.00000   0.00002       NaN   0.00000      0.00000   
M_RAVE_1             0.00002   0.00000   0.00000       NaN      0.00122   
M_RAVE_0.25          0.22330   0.00000   0.00000   0.00122          NaN   
Add_M_RAVE_sqrt2     0.00000   0.00000   0.00069   0.15605          NaN   

                  Add_M_RAVE_sqrt2  
M_RAVE_0.5                 0.00000  
M_RAVE_3                   0.00000  
M_RAVE_2                   0.00069  
M_RAVE_1                   0.15605  
M_RAVE_0.25                    NaN  
Add_M_RAVE_sqrt2               NaN  
                  M_RAVE_0.5  M_RAVE_3  M_RAVE_2  M_RAVE_1  M_RAVE_0.25  \
M_RAV

In [1]:
#t-test: https://www.hackdeploy.com/python-t-test-a-friendly-guide/

import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp
from scipy import stats as spst
from datetime import date


print(os.path.abspath(os.getcwd()))

logs_path = "logs"
join = "/"
exp = "1_EXP_MCTS_Param"

def significance_test_allvsall(exp_name, threshold = 0.05):
   data =  pd.read_csv(logs_path + join + exp_name + join + "PlayerStats.csv")
   first = True
   lista = []
   for _ in range(len(data)):
      lista.append(first)
      if first: first = False
      else: first = True
   data["IsFirstPlayer"] = lista
   #filtered_data = data[data["IsFirstPlayer"]==True]

   agents = data["Player"].unique()
   na = len(agents)
   print("Agents: ", agents)
   all_colors = ["blue","orange","green","yellow","red","black","pink","brown","purple","gray","goldenrod","magenta","#0AD","6C4" ]
   assert(na <= len(all_colors))
   agents_legends = [a+"_as_1st" for a in agents] + [a+"_as_2nd" for a in agents]
   colors = {a:all_colors[i] for i,a in enumerate(agents_legends)}

   ##Scores
   s_pvals = {}
   s_sig_dict = {}

   checked_players = []
   added_legends = []
   
   plot = make_subplots(rows=na+1, cols=na+1
            #,shared_xaxes=True
            ,shared_yaxes=True
            #,subplot_titles=["Opponent's combined score","Opponent's combined score difference","Opponent's combined score proportion"]
            #,row_heights=[4 for _ in exps_names]
            #,vertical_spacing=0.3
            ,print_grid=True
            ,x_title="Player"
            )
   

   #filtered_data = data
   to_plot = {name:[] for name in ["A1","A2","row","column","nr","nc"]}
   for nc, column in enumerate(agents): #the row agent
      s_player_significants = []
      s_player_pvals = []
      for nr, row in enumerate(agents): #the column agent
         if row != column:
            if row in checked_players: #if in the upper triangle of the matrix
               #el volteado
               group_separator = "_as_2nd"
               row_filtered_data = data[(data["IsFirstPlayer"]==False) & (data["Player"]==row) & (data["Opponent"]==column)] #S2,1
               row_scores = row_filtered_data["PlayerScore"]

               column_filtered_data = data[(data["IsFirstPlayer"]==False) & (data["Player"]==column) & (data["Opponent"]==row)] #S2,2
               column_scores = column_filtered_data["PlayerScore"]

            else:
               group_separator = "_as_1st"
               row_filtered_data = data[(data["IsFirstPlayer"]==True) & (data["Player"]==row) & (data["Opponent"]==column)] #S1,1
               row_scores = row_filtered_data["PlayerScore"]

               column_filtered_data = data[(data["IsFirstPlayer"]==True) & (data["Player"]==column) & (data["Opponent"]==row)] #S1,2
               column_scores = column_filtered_data["PlayerScore"]

            s_Stat, s_pValue = spst.ttest_ind(row_scores, column_scores, equal_var = False)
            s_player_significants.append(s_pValue<threshold)
            s_player_pvals.append(s_pValue)
            print("Upper: row: ", row, ", column:", column, ", lenghts:", str(len(row_scores)), str(len(column_scores)))
            row_legend = row+group_separator not in added_legends
            col_legend = column+group_separator not in added_legends
            plot.add_trace(
                go.Box(
                    y=row_scores,
                    x=[row for _ in range(len(row_scores))],
                    name=row+group_separator,
                    legendgroup=row+group_separator,
                    marker_color=colors[row+group_separator],
                    showlegend=row_legend
                    ),
                row = nr+1,
                col = nc+1
                )
            plot.add_trace(
                go.Box(
                    y=column_scores,
                    x=[column for _ in range(len(column_scores))],
                    name=column+group_separator,
                    legendgroup=column+group_separator,
                    marker_color=colors[column+group_separator],
                    showlegend=col_legend
                    ),
                row = nr+1,
                col = nc+1
                )
            added_legends = added_legends + [column+group_separator, row+group_separator]
            added_legends = list(set(added_legends))
         else:
            s_player_significants.append(None)
            s_player_pvals.append(None)
            #print("Upper: row: ", row, ", column:", column, ", lenghts:", None, None)
         

      checked_players.append(column)

      print("Adding column: ", column, ", values: ", s_player_pvals)
      s_sig_dict[column] = s_player_significants
      s_pvals[column] = s_player_pvals

   plot.update_layout(
      #boxmode='group'
      #,
      title_text="Scores distribution"
      #,xaxis_title="Player"
      ,yaxis_title="Score"
      #,legend_title="Player"
      ,autosize=False
      ,width=1000
      ,height=1000)
   #plot.update_xaxes(title_text = "")
   plot.show()
   

   s_sig_data = pd.DataFrame(s_sig_dict, index=agents)
   s_pvals_data = pd.DataFrame(s_pvals, index=agents).round(5)

   today = date.today()
   d = today.strftime("_%d_%m_%Y_%H_%M_%S")

   s_sig_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score_significance"+ d+".csv")
   s_pvals_data.to_csv(logs_path + join + "analysis" + join + exp_name + "_score_pvalues"+ d+".csv")
      
   return s_pvals_data



d:\Users\fredx\Documents\Gits\mcts_uct_fred


In [3]:
out = significance_test_allvsall("3_EXP_Minimax")
#out = significance_test_allvsall("2_EXP_RAVE_Param")
#out = significance_test_allvsall("1_EXP_MCTS_Param")
print(out)

Agents:  ['Star2' 'Star2.5' 'Star1']
This is the format of your plot grid:
[ (1,1) x,y     ]  [ (1,2) x2,y2   ]  [ (1,3) x3,y3   ]  [ (1,4) x4,y4   ]
[ (2,1) x5,y5   ]  [ (2,2) x6,y6   ]  [ (2,3) x7,y7   ]  [ (2,4) x8,y8   ]
[ (3,1) x9,y9   ]  [ (3,2) x10,y10 ]  [ (3,3) x11,y11 ]  [ (3,4) x12,y12 ]
[ (4,1) x13,y13 ]  [ (4,2) x14,y14 ]  [ (4,3) x15,y15 ]  [ (4,4) x16,y16 ]

Upper: row:  Star2.5 , column: Star2 , lenghts: 25 25
Upper: row:  Star1 , column: Star2 , lenghts: 25 25
Adding column:  Star2 , values:  [None, 0.5413218193785163, 0.3562791632296757]
Upper: row:  Star2 , column: Star2.5 , lenghts: 25 25
Upper: row:  Star1 , column: Star2.5 , lenghts: 25 25
Adding column:  Star2.5 , values:  [0.6158348445221855, None, 0.05495598093718976]
Upper: row:  Star2 , column: Star1 , lenghts: 25 25
Upper: row:  Star2.5 , column: Star1 , lenghts: 25 25
Adding column:  Star1 , values:  [0.038144875763080434, 0.024859630305989394, None]


           Star2  Star2.5    Star1
Star2        NaN  0.61583  0.03814
Star2.5  0.54132      NaN  0.02486
Star1    0.35628  0.05496      NaN


In [6]:
import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp
from scipy import stats as spst
from datetime import date


print(os.path.abspath(os.getcwd()))

logs_path = "logs"
join = "/"
#exp = "1_EXP_MCTS_Param"
#exp = "3_EXP_Minimax"
#exp = "2_EXP_RAVE_Param"
exp = "4_EXP_All_Games"

def gather_scores(exp_name, file_name = None):

   #get data
   if file_name is None:
      data =  pd.read_csv(logs_path + join + exp_name + join + "PlayerStats.csv")
   else:
      data =  pd.read_csv(logs_path + join + exp_name + join + file_name)
   
   #Pre-processing
   first = True
   lista = []
   for _ in range(len(data)):
      lista.append(first)
      if first: first = False
      else: first = True
   data["PlayerWasFirst"] = lista
   data['Player'] = data['Player'].str.replace('Add_','')
   data['Opponent'] = data['Opponent'].str.replace('Add_','')

   #prepare variables, order (not used currently)
   if exp_name=="1_EXP_MCTS_Param":
      agents = ["MCTS_0.25","MCTS_0.5","MCTS_1","MCTS_sqrt2","MCTS_2","MCTS_3"]
   else:
      agents = data["Player"].unique()
   print("Agents: ", agents)

   #calculations
   data["Difference"] = data["PlayerScore"]-data["OpponentScore"]
   data["CityScore"] = data["CompleteCityScore"]+data["IncompleteCityScore"]
   data["RoadScore"] = data["CompleteRoadScore"]+data["IncompleteRoadScore"]
   data["MonasteryScore"] = data["CompleteMonasteryScore"]+data["IncompleteMonasteryScore"]

   #filtering and grouping
   #t_data = data[data["PlayerWasFirst"]==True]
   data_split = data.loc[:,["Player","Opponent","PlayerScore","Difference","CityScore","RoadScore","MonasteryScore","Game","PlayerWasFirst"]]
   data_split = data_split.sort_values(by=["Player","Opponent"])
   
   data_isf = data.loc[:,["Player","Opponent","PlayerScore","Difference","CityScore","RoadScore","MonasteryScore","PlayerWasFirst"]]
   data = data.loc[:,["Player","Opponent","PlayerScore","Difference","CityScore","RoadScore","MonasteryScore"]]
   
   final_df = data.groupby(["Player","Opponent"]).agg([np.mean, np.std, np.var]).round(3)
   final_df_isf = data_isf.groupby(["Player","Opponent","PlayerWasFirst"]).agg([np.mean, np.std, np.var]).round(3)

   #save to a file
   today = date.today()
   d = today.strftime("_%d_%m_%Y_%H_%M_%S")

   #to file
   data_split.to_csv(logs_path + join + "analysis" + join + exp_name + "_scores"+ d+".csv", index=False)
   #final_df_isf.to_csv(logs_path + join + "analysis" + join + exp_name + "_gather_scores_isf"+ d+".csv")
   final_df.to_csv(logs_path + join + "analysis" + join + exp_name + "_gather_scores"+ d+".csv", index=False)
   final_df_isf.to_csv(logs_path + join + "analysis" + join + exp_name + "_gather_scores_isf"+ d+".csv", index=False)
      
   return final_df

df = gather_scores(exp, "ScoreAnalysis_PlayerStats.csv")
df.head()


d:\Users\fredx\Documents\Gits\mcts_uct_fred
Agents:  ['ES_B_MCTS' 'ES_B_S_MCTS' 'M_RAVE_0.25' 'Star1' 'Random' 'M_RAVE_0.5'
 'ES_MCTS' 'MCTS_0.5_400' 'MCTS_sq2_400' 'MCTS_0.52800' 'MCTS_sq2_2800'
 'M_RAVE_0.52800' 'M_RAVE_0.252800']


PlayerScore                  Difference          \
                               mean     std      var       mean     std   
Player    Opponent                                                        
ES_B_MCTS ES_B_S_MCTS        77.733  17.483  305.651     -0.933  22.221   
          ES_MCTS            90.967  13.229  174.999     43.067  20.184   
          MCTS_0.52800       77.367  16.311  266.033      1.067  19.172   
          MCTS_0.5_400       78.533  17.733  314.464      9.433  24.933   
          MCTS_sq2_2800      75.367  11.976  143.413    -12.967  19.455   

                                 CityScore                  RoadScore         \
                             var      mean     std      var      mean    std   
Player    Opponent                                                             
ES_B_MCTS ES_B_S_MCTS    493.789    33.133   9.726   94.602    16.767  7.454   
          ES_MCTS        407.375    45.867  10.543  111.154    17.867  7.123   
          MCTS_0.52800   367.582    31.633   9.817   96.378    19.500  5.824   
          MCTS_0.5_400   621.633    37.533  13.240  175.292    16.533  6.986   
          MCTS_sq2_2800  378.516    33.800   9.866   97.338    17.800  6.697   

                                MonasteryScore                 
                            var           mean    std     var  
Player    Opponent                                             
ES_B_MCTS ES_B_S_MCTS    55.564         10.033  8.728  76.171  
          ES_MCTS        50.740          9.933  7.007  49.099  
          MCTS_0.52800   33.914          7.933  7.492  56.133  
          MCTS_0.5_400   48.809          8.367  7.627  58.171  
          MCTS_sq2_2800  44.855          9.067  7.529  56.685

In [28]:
import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
#import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp
from scipy import stats as spst
from datetime import date

logs_path = "logs"
join = "/"
#exp = "1_EXP_MCTS_Param"
#exp = "3_EXP_Minimax"
exp = "2_EXP_RAVE_Param"

def formula_analysis(filtered_data, title, n_formulas=5, spaced="evenly", identifier = "black"):
    plot = go.Figure()
    x = filtered_data["Turn"]
    y = filtered_data["NumberNodes"]
    plot.add_trace(go.Box(
        name="Number of Nodes",x=x,y=y
        ,legendgroup='group1'
        ,showlegend=False
        ,marker_color = "black"
        ))
    plot.add_trace(go.Scatter(x=x, y=[13 for _ in x],
                    mode='lines',legendgroup='group1'
                    ,showlegend=False,
                    name='UCT'
                    ,marker_color = "black"))

    #select random formula
    functions = []
    turns = [int(max(x)/n_formulas)*i+1 for i in range(n_formulas)]
    for t in turns:
        temp_df = filtered_data[filtered_data["Turn"]==t]
        cont = True
        while(cont):
            random_index = np.random.randint(0,len(temp_df)-1)
            if temp_df["NumberNodes"].values[random_index] < 25 and temp_df["NumberNodes"].values[random_index] > 9:
                functions.append((t
                    ,temp_df["NumberNodes"].values[random_index]
                    ,temp_df["Function"].values[random_index]))
                cont = False
            #else: print("Finding another formula")

    markers = ["square", "diamond","cross","x","triangle-up","triangle-down","star","star-square","corcle-cross","pentagon"]
    for marker_id, f in enumerate(functions):#enumerate([[int(max(x)/n_formulas)*i+1] for i in range(n_formulas)]):
        x_formula = [f[0]]
        y_formula = [f[1]]
        formula_text = f[2]
        plot.add_trace(go.Scatter(
                        x=x_formula
                        ,y=y_formula
                        ,mode='markers'
                        ,legendgroup='group1'
                        ,showlegend=True
                        ,name='<b>'+formula_text+'</b>'#""#str(filtered_data["Function"].iloc[x_formula]).split("Name")[0]
                        ,marker_symbol = markers[marker_id] + "-open-dot"
                        #,marker_color = "black"
                        #,marker_size=9
                        ,marker=dict(
                            color=identifier,#"red",#'rgba(135, 206, 250, 0.5)',
                            size=10,
                            line=dict(
                                color='MediumPurple',
                                width=2.5
                            )
                        )))

    plot.update_layout(
                #title_text=title
                #,title_x=0.5
                #,title_y=1
                #xaxis_title="Turn"
                #,yaxis_title="Nodes"
                autosize=False
                ,width=700
                ,height=350
                ,plot_bgcolor='rgba(0,0,0,0)'
                ,legend=dict(
                    #title = "Formula",
                    #orientation="h",
                    #yanchor="top",
                    y=-0.65,
                    xanchor="center",
                    x=0.5,  
                    font = dict(family = "Arial", size = 14, color = "black"),
                    #bordercolor="LightSteelBlue",
                    borderwidth=2,
                    itemsizing='trace',
                    itemwidth = 30
                    )  
                )       
    plot['layout'].update(margin=dict(
                                        l=20,
                                        r=10,
                                        #b=0,
                                        t=10))    
    plot["layout"]["xaxis"]["range"] = [0.1, 37]  
    plot["layout"]["yaxis"]["tickfont"]["size"] = 13 ##dict(family = 'Old Standard TT, serif',size = 14,color = 'black'),
    plot["layout"]["yaxis"]["tickfont"]["color"] = "black"
    plot["layout"]["xaxis"]["tickfont"]["size"] = 13 ##dict(family = 'Old Standard TT, serif',size = 14,color = 'black'),
    plot["layout"]["xaxis"]["tickfont"]["color"] = "black"
    #plot['layout'].legend.x = 0 
    #plot['layout'].legend.y = -2 
    plot.update_xaxes(anchor="free"
                    ,position=0.04)
    plot.update_xaxes(showline=True, linewidth=1.5, linecolor='black', 
                  #zeroline=True, 
                  #zerolinewidth=1.5, zerolinecolor='black',

                )
    plot.update_yaxes(showline=True, linewidth=1.5, linecolor='black', mirror=True
                  #gridcolor='black', gridwidth=1,
                   #zeroline=True, 
                   #zerolinewidth=1.5, zerolinecolor='black',
    )

    plot.add_shape(
        # Rectangle with reference to the plot
            type="rect",
            xref="paper",
            yref="paper",
            x0=0,
            y0=1,
            x1=1.0,
            y1=1.0,
            line=dict(
                color="black",
                 width=1,
             )
         )
    """
    plot.add_annotation(
        x=0,
        y=-1,
        xref="paper",
        yref="paper",
        text="            sdhyfgauyrewgbayuergbnaeurgnaiurgnaiuerbmiebrmnaeilrbmaoiergarg",
        showarrow=False,
        font=dict(
            #family="Courier New, monospace",
            size=12,
            color="black"
            ),
        align="left",
        arrowhead=2,
        arrowsize=1,
        arrowwidth=2,
        arrowcolor="#636363",
        ax=20,
        ay=-30,
        bordercolor="black",
        borderwidth=2,
        borderpad=4,
        #bgcolor="#ff7f0e",
        opacity=0.8
        )
    """
    plot.show()
    plot.write_image(agent_name + identifier + ".svg", width=1920, height=1080)
    #plot.write_image(title+ ".pdf")


np.random.seed(13)
full_df =  pd.read_csv(logs_path + join + "4_EXP_All_Games" + join + "CollectedEvolvedUCT.csv")
agents = list(full_df["Name"].unique())
for agent in agents:
    filtered_df = full_df[full_df["Name"]==agent]
    if agent == "ES_B_S_MCTS": 
        agent_name = "SIEA_MCTS"
        #np.random.seed(2)
    if agent == "ES_B_MCTS": 
        agent_name = "EA_MCTS"
        #np.random.seed(3)ff
    if agent == "ES_MCTS": 
        agent_name = "EA_p_MCTS"
        #np.random.seed(4)
    formula_analysis(filtered_df, agent_name, identifier = "black")

In [4]:
import pandas as pd
import os
import numpy as np
import math
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "vscode"
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date
from collections import OrderedDict
import time
import multiprocessing as mp
import ast
import random
import statistics as stats
import matplotlib.pyplot as plt
from collections import defaultdict
import scipy as sp
from scipy import stats as spst
from datetime import date

logs_path = "logs"
join = "/"

def create_league_table(data, exp_name):
   #pre-processing
   first = True
   lista = []
   for _ in range(len(data)):
      lista.append(first)
      if first: first = False
      else: first = True
   data["PlayerWasFirst"] = lista
   data['Player'] = data['Player'].str.replace('Add_','')
   data['Opponent'] = data['Opponent'].str.replace('Add_','')
   data['Differences'] = data['PlayerScore']-data["OpponentScore"]

   dict_holder = defaultdict(lambda:[])
   agents = data["Player"].unique()
   for agent in agents:
      filetered_data = data[data["Player"]==agent]
      dict_holder["MatchesPlayed"].append(len(filetered_data[filetered_data["Game"]==1]))
      dict_holder["Player"].append(agent)
      ds = 0
      ws = 0
      ls = 0
      points = 0
      bwp = 0
      blp = 0
      pds = 0
      for opponent in agents:
         if agent != opponent:
            for isfirst in [True, False]:
               uniques_filetered_data = filetered_data[filetered_data["PlayerWasFirst"]==isfirst]
               opponent_filtered_data = uniques_filetered_data[uniques_filetered_data["Opponent"]==opponent]
               if len(opponent_filtered_data) == 0:
                  print(agent, "as first:",str(isfirst), "vs ", opponent, ": ",len(opponent_filtered_data))
               else:
                  pds += round(sum(opponent_filtered_data["Differences"])/len(opponent_filtered_data),3)
                  wins = len(opponent_filtered_data[opponent_filtered_data["Win"]==1])
                  losses = len(opponent_filtered_data[opponent_filtered_data["Loss"]==1])
                  if wins > losses:
                     ws += 1
                     points += 4
                     if (wins/(wins+losses) >= 0.75):
                        points += 1
                        bwp += 1
                  elif losses > wins:
                     ls += 1
                     if (losses/(wins+losses) <= 0.55):
                        points += 1
                        blp += 1
                  else:
                     ds += 1
                     points += 2
      dict_holder["Points"].append(points)
      dict_holder["BWP"].append(bwp)
      dict_holder["BLP"].append(blp)
      dict_holder["W"].append(ws)
      dict_holder["L"].append(ls)
      dict_holder["D"].append(ds)
      dict_holder["PD"].append(pds)
      #for opponent in agents:
      #   opponent_filtered_data = filetered_data[filetered_data["Opponent"]==opponent]
      #agent_dict["BWP"] = sum(filetered_data["Differences"])


   final_df = pd.DataFrame(dict_holder)
   final_df.sort_values(by=["Points","PD"])
   today = date.today()
   d = today.strftime("_%d_%m_%Y_%H_%M_%S")
   final_df.to_csv(logs_path + join + "analysis" + join + exp_name + "_NewLeagueTable"+ d+".csv")

exp_name = "4_EXP_All_Games"
output_name = "LAST"
full_df =  pd.read_csv(logs_path + join + exp_name + join + "ScoreAnalysis_PlayerStats.csv")
create_league_table(full_df, output_name)
   